# X-ray crystallography data visualisation

In [1]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import os
import time
from tqdm.notebook import tqdm
from watchdog.observers import Observer
from watchdog.events import FileSystemEventHandler, FileCreatedEvent

In [2]:
# enter directory we will be watching for new files
# then run the while loop and run the generator function in C5_Simulator.ipynb
data_directory = "../data/target"
number_of_curves = 10

# logarithmic=True
# mode = "log" / "linear" # all 3 scales
# color_map = 'viridis'
# num_frames = 100
# delay = 0.1
# option to cut noise from data -> function to drop first and end values
# below zero on logarithmic scale is OK

drop_first = 1
drop_last = 1
cut_values_below = 0.8

In [4]:
from collections import deque 

timestr = time.strftime("%Y.%m.%d-%H.%M.%S")

class Watcher:

    def __init__(self, directory_to_watch, watch_time_interval=0.5):
        self.observer = Observer()
        self.directory_to_watch = directory_to_watch
        self.watch_time_interval = watch_time_interval

    def run(self):
        event_handler = Handler()
        self.observer.schedule(event_handler, self.directory_to_watch, recursive=True)
        self.observer.start()
        try:
            while True:
                time.sleep(self.watch_time_interval)
                
        except:
            self.observer.stop()
            print("Error")

        self.observer.join()


class Handler(FileSystemEventHandler):
    
    def __init__(self):
        self.path_strings = []

    def on_created(self, event):

        if isinstance(event, FileCreatedEvent):
            
            self.path_strings.append(event.src_path)
            self.path_strings = self.path_strings[-number_of_curves:]


w = Watcher(data_directory, watch_time_interval=0.5)
w.run()


Error


In [7]:
import pandas as pd

def get_trace(datafile_path, time=11):
    # read data from single .dat file
    data = np.loadtxt(datafile_path)
    y_data = data[:,1][data[:,1] > cut_values_below][drop_last:-drop_first]
    x_data = data[:,0][data[:,1] > cut_values_below][drop_last:-drop_first]
    y_data[-1] = None
    x_data[-1] = None
    
    new_curve = pd.DataFrame.from_dict({
        'I': x_data,
        'q': y_data,
        't': [time]*(len(x_data))
    })
    
    return new_curve

In [38]:
import plotly.graph_objects as go

def figure_function(data_x, data_y, data_z, mode='linear'):
    data = go.Scatter3d(
    x=data_x,
    y=data_y,
    z=data_z,
    mode='lines',
    # marker=dict(
    #     color=data_dataframe['y'],
    #     size=2,
    # )
    line=dict(
        color=data_x,
    ),
    )

    mode = 'log' # log or linear

    layout = go.Layout(
        title='3D Scatter Plot from .dat files',
        scene=dict(
            xaxis=dict(
                title='q_A^-1',
                #backgroundcolor="rgb(200, 200, 230)",
                            gridcolor="white",
                            showbackground=True,
                            dtick=0.5,
                type=mode
            ),
            yaxis=dict(
                title='t',
                
                            #backgroundcolor="rgb(230, 200,230)",
                            gridcolor="white",
                            showbackground=True,
                #range=[1,20],
                # rangeslider=dict(
                #     visible=True
                # )
                autorange=True,
                dtick=10,
                type=mode
                
            ),
            zaxis=dict(
                title='I',
                
                            #backgroundcolor="rgb(230, 230,200)",
                            gridcolor="white",
                            showbackground=True,
                            dtick=0.5,
                            type=mode
                            
            ),
            
            aspectmode="manual", #data
            aspectratio = dict(x=2, y=5, z=1)
        ),
        autosize=True,
        width=800, #1200
        height=600, #800
    )
    fig = go.Figure(data=data, layout=layout)

    return fig

fig = figure_function(data_dataframe['I'], data_dataframe['t'], data_dataframe['q'])
fig.update_traces(connectgaps=False) 
fig.show()


In [41]:
# for every .dat file in folder indexed from 000001 to 001000 load each file via np.loadtxt)
import pandas as pd
data_dataframe = pd.DataFrame(columns=["I", "q", "t"])
data_directory = "../data/source/"

fig = figure_function(data_dataframe['I'], data_dataframe['t'], data_dataframe['q'])
fig.update_traces(connectgaps=False) 
fig.show()

for k in range(50):
    time.sleep(1)
    for i, datafile in enumerate(sorted(os.listdir(data_directory))[k:number_of_curves+k]):
        if datafile.endswith(".dat"):
            datafile_path = os.path.join(data_directory, datafile)
            new_curve = get_trace(datafile_path, time=i)
            data_dataframe = data_dataframe.append(new_curve, ignore_index=True)
    fig.update_traces(go.Scatter3d(
    x=data_dataframe['I'],
    y=data_dataframe['t'],
    z=data_dataframe['q'],
    mode='lines',
    # marker=dict(
    #     color=data_dataframe['y'],
    #     size=2,
    # )
    line=dict(
        color=data_dataframe['I'],
    ),
    ))
    #fig.show()
        
    

KeyboardInterrupt: 

In [28]:
# for every .dat file in folder indexed from 000001 to 001000 load each file via np.loadtxt)
import pandas as pd
data_dataframe = pd.DataFrame(columns=["I", "q", "t"])
data_directory = "../data/source/"

for i, datafile in enumerate(sorted(os.listdir(data_directory))[10:number_of_curves+10]):
    if datafile.endswith(".dat"):
        data = np.loadtxt(data_directory + "/" + datafile)
        y_data = data[:,1][data[:,1] > cut_values_below][drop_last:-drop_first]
        x_data = data[:,0][data[:,1] > cut_values_below][drop_last:-drop_first]
        y_data[-1] = None
        x_data[-1] = None
        
        new_curve = pd.DataFrame.from_dict({
            'I': x_data,
            'q': y_data,
            't': [i]*(len(x_data))
        })
        data_dataframe = data_dataframe.append(new_curve, ignore_index=True)

In [36]:
fig.update_traces(go.Scatter3d(
    x=data_dataframe['I'],
    y=data_dataframe['t'],
    z=data_dataframe['q'],
    mode='lines',
    # marker=dict(
    #     color=data_dataframe['y'],
    #     size=2,
    # )
    line=dict(
        color=data_dataframe['I'],
    ),
    ))
fig.show()


In [21]:
new_file = data_directory + "/" + sorted(os.listdir(data_directory))[11]
new_file 

'../data/source//C5_mesh_1_data.cbf000012.dat'

In [37]:
# trace = get_trace(new_file, time=11)
# fig.add_trace(go.Scatter3d(
#     x=trace["I"],
#     y=trace["q"],
#     z=trace["t"],))
# fig.show()

In [ ]:
fig.update_traces

In [ ]:
from dash import Dash, dcc, html, Input, Output
import pandas as pd
from jupyter_dash import JupyterDash

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = JupyterDash(__name__, external_stylesheets=external_stylesheets)

app.layout = html.Div([
    html.H4('3D Scatter Plot from .dat files'),
    dcc.Graph(id="graph"),
    dcc.Interval(interval=500, id="interval", n_intervals=1),
    # dcc.RangeSlider(
    #     id='range-slider',
    #     min=0, max=2.5, step=0.1,
    #     marks={0: '0', 2.5: '2.5'},
    #     value=[0.5, 2]
    # ),
])

@app.callback(
    Output("graph", "figure"), 
    Input('interval', 'n_intervals')
    #Input("range-slider", "value"))
def update_bar_chart(n_intervals):
    last_row = n_intervals*100
    stored_data = df.iloc[0:last_row]

    fig = px.scatter_3d(df[mask], 
        x='sepal_length', y='sepal_width', z='petal_width',
        color="species", hover_data=['petal_width'])
    return fig

app.run_server(mode='inline')

In [14]:
from dash import Dash, dcc, html, Input, Output
import pandas as pd
from jupyter_dash import JupyterDash

import json

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = JupyterDash(__name__, external_stylesheets=external_stylesheets)

fig = figure_function(data_dataframe['I'], data_dataframe['t'], data_dataframe['q'])

app.layout = html.Div([
    dcc.Graph(
        id='clientside-graph',
        figure=fig
    ),
    
    dcc.Store(
        id='clientside-figure-store'
    ),
    # dcc.Store(
    #     id='clientside-figure-store',
    #     data=[{
    #         'x': data_dataframe['x'],
    #         'y': data_dataframe['y'],
    #         'z': data_dataframe['z']
    #     }]
    # ),
    'Graph scale',
    dcc.RadioItems(
        ['linear', 'log'],
        'linear',
        id='clientside-graph-scale'
    )
])


@app.callback(
    Output('clientside-figure-store', 'data'),
    #Input('clientside-graph-indicator', 'value'),
    #Input('clientside-graph-scale', 'scale')
)
def update_store_data(scale):
    fig = figure_function(data_dataframe['I'], data_dataframe['t'], data_dataframe['q'])
    return fig
    # return [{
    #     'x': data_dataframe['x'],
    #     'y': data_dataframe['y'],
    #     'z' : data_dataframe['z'],
    #     'mode': 'markers'
    # }]


app.clientside_callback(
    
    """
    function(figure, scale) {
        if(figure === undefined) {
            return {'data': [], 'layout': {}};
        }
        const fig = Object.assign({}, figure, {
            'data : data,
            'layout': {
                ...figure.layout,
                'yaxis': {
                    ...figure.layout.yaxis, type: scale
                },
                'xaxis': {
                    ...figure.layout.yaxis, type: scale
                },
                'zaxis': {
                    ...figure.layout.yaxis, type: scale
                }
             }
        });
        return fig;
    }
    """,
    # """
    # function(data, scale) {
    #     return {
    #         'data': data,
    #         'layout': {
    #              'yaxis': {'type': scale}
    #              'xaxis': {'type': scale}
    #              'zaxis': {'type': scale}
    #          }
    #     }
    # }
    # """,
    Output('clientside-graph', 'figure'),
    Input('clientside-figure-store', 'data'),
    Input('clientside-graph-scale', 'value')
)


# @app.callback(
#     Output('clientside-figure-json', 'children'),
#     Input('clientside-figure-store', 'data')
# )
# def generated_figure_json(data):
#     return '```\n'+json.dumps(data, indent=2)+'\n```'


app.run_server(mode="inline", use_reloader=False)

---------------------------------------------------------------------------
KeyError                                  Traceback (most recent call last)
File ~/Library/CloudStorage/OneDrive-UniverzitaKarlova/Github/Time resolved X-ray diffraction crystallography/eli_plotter_env/lib/python3.9/site-packages/dash/dash.py:1208, in Dash.dispatch(
    self=<jupyter_dash.jupyter_app.JupyterDash object>
)
   1207 try:
-> 1208     cb = self.callback_map[output]
        output = 'clientside-store-data.data'
        self = <jupyter_dash.jupyter_app.JupyterDash object at 0x1143abbe0>
        self.callback_map = {'clientside-figure-store.data': {'inputs': [], 'state': [], 'outputs_indices': 0, 'inputs_state_indices': [], 'long': None, 'output': <Output `clientside-figure-store.data`>, 'raw_inputs': [], 'callback': <function update_store_data at 0x17610a040>}, 'clientside-graph.figure': {'inputs': [{'id': 'clientside-figure-store', 'property': 'data'}, {'id': 'clientside-graph-scale', 'property': 'va

In [ ]:
import dash
import dash_html_components as html
import dash_core_components as dcc
import numpy as np
from jupyter_dash import JupyterDash
from dash.dependencies import Input, Output, State

# Example data (a circle).
resolution = 1000
t = np.linspace(0, np.pi * 2, resolution)
x, y = np.cos(t), np.sin(t)
# Example app.
figure = dict(data=[{'x': [], 'y': []}], layout=dict(xaxis=dict(range=[-1, 1]), yaxis=dict(range=[-1, 1])))
app = JupyterDash(__name__, update_title=None)  # remove "Updating..." from title
app.layout = html.Div([
    dcc.Graph(id='graph', figure=dict(figure)), dcc.Interval(id="interval", interval=25),
    dcc.Store(id='offset', data=0), dcc.Store(id='store', data=dict(x=x, y=y, resolution=resolution)),
])
app.clientside_callback(
    """
    function (n_intervals, data, offset) {
        offset = offset % data.x.length;
        const end = Math.min((offset + 10), data.x.length);
        return [[{x: [data.x.slice(offset, end)], y: [data.y.slice(offset, end)]}, [0], 500], end]
    }
    """,
    [Output('graph', 'extendData'), Output('offset', 'data')],
    [Input('interval', 'n_intervals')], [State('store', 'data'), State('offset', 'data')]
)

app.run_server(mode='inline')

In [1]:
import dash
import dash_html_components as html
import dash_core_components as dcc
import numpy as np
from jupyter_dash import JupyterDash
from dash.dependencies import Input, Output, State

# Example data (a circle).
resolution = 1000
t = np.linspace(0, np.pi * 2, resolution)
x, y = np.cos(t), np.sin(t)
# Example app.
figure = dict(data=[{'x': [], 'y': []}], layout=dict(xaxis=dict(range=[-1, 1]), yaxis=dict(range=[-1, 1])))
app = JupyterDash(__name__, update_title=None)  # remove "Updating..." from title
app.layout = html.Div([
    dcc.Graph(id='graph', figure=dict(figure)), dcc.Interval(id="interval", interval=25),
    dcc.Store(id='offset', data=0), dcc.Store(id='store', data=dict(x=x, y=y, resolution=resolution)),
])
app.clientside_callback(
    """
    function (n_intervals, data, offset) {
        offset = offset % data.x.length;
        const end = Math.min((offset + 10), data.x.length);
        return [[{x: [data.x.slice(offset, end)], y: [data.y.slice(offset, end)]}, [0], 500], end]
    }
    """,
    [Output('graph', 'extendData'), Output('offset', 'data')],
    [Input('interval', 'n_intervals')], [State('store', 'data'), State('offset', 'data')]
)

app.run_server(mode='inline')

/var/folders/bh/q7z_19rs0wl0v6955b12l3d00000gn/T/ipykernel_5298/2418304058.py:2: UserWarning: 
The dash_html_components package is deprecated. Please replace
`import dash_html_components as html` with `from dash import html`
  import dash_html_components as html
/var/folders/bh/q7z_19rs0wl0v6955b12l3d00000gn/T/ipykernel_5298/2418304058.py:3: UserWarning: 
The dash_core_components package is deprecated. Please replace
`import dash_core_components as dcc` with `from dash import dcc`
  import dash_core_components as dcc


In [9]:
from dash import Dash, dcc, html, Input, Output
import pandas as pd
import json
from jupyter_dash import JupyterDash

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

# JupyterDash.infer_jupyter_proxy_config()
app = JupyterDash(__name__, external_stylesheets=external_stylesheets)

# Rewrite Scatter3d into Dash as clientside callback with scale option
app.layout = html.Div([
    html.Div(
      id='clientside-content', children="Data will be here"  
    ),
    dcc.Store(
        id='clientside-store-data', data={}
    ),
    dcc.Interval(
        id='serverside-interval',
        interval=2000,
        n_intervals=1
    ),
    dcc.Interval(
        id='clientside-interval',
        n_interval=1,
        interval=25 #miliseconds
    )
    # dcc.RadioItems(
    #     ['linear', 'log'],
    #     'linear',
    #     id='clientside-graph-scale-px'
    # ),
    # html.Hr(),
    # html.Details([
    #     html.Summary('Contents of figure storage'),
    #     dcc.Markdown(
    #         id='clientside-figure-json-px'
    #     )
    # ])
])

@app.callback(
    Output('clientside-store-data', 'data'),
    Input('clientside-graph-indicator-px', 'value'),
    Input('clientside-graph-country-px', 'value')
)
def update_figure(indicator, country):
    figure = figure_function(data_dataframe['x'], data_dataframe['y'], data_dataframe['z'])
    return figure

app.clientside_callback(
    """
    function(figure, scale) {
        if(figure === undefined) {
            return {'data': [], 'layout': {}};
        }
        const fig = Object.assign({}, figure, {
            'layout': {
                ...figure.layout,
                'yaxis': {
                    ...figure.layout.yaxis, type: scale
                }
             }
        });
        return fig;
    }
    """,
    Output('clientside-graph-px', 'figure'),
    Input('clientside-store-data', 'data'),
    Input('clientside-graph-scale-px', 'value')
)

app.run_server(mode="inline") # port=8050


: 

In [9]:
df = px.data.gapminder().query("continent=='Europe'")
df.head()

country continent  year  lifeExp      pop    gdpPercap iso_alpha  iso_num
12  Albania    Europe  1952    55.23  1282697  1601.056136       ALB        8
13  Albania    Europe  1957    59.28  1476505  1942.284244       ALB        8
14  Albania    Europe  1962    64.82  1728137  2312.888958       ALB        8
15  Albania    Europe  1967    66.22  1984060  2760.196931       ALB        8
16  Albania    Europe  1972    67.69  2263554  3313.422188       ALB        8

In [10]:
fig = px.line_3d(df, x="gdpPercap", y="pop", z="year", color='country')
fig.show()

In [8]:
import plotly.express as px
df = px.data.gapminder().query("country=='Brazil'")
fig = px.line_3d(df, x="gdpPercap", y="pop", z="year")
fig.show()

In [7]:
import plotly.graph_objects as go
import pandas as pd

df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/finance-charts-apple.csv')

fig = go.Figure(go.Scatter(
    x = df['Date'],
    y = df['mavg']
))

fig.update_xaxes(
    rangeslider_visible=True,
    # tickformatstops = [
    #     dict(dtickrange=[None, 1000], value="%H:%M:%S.%L ms"),
    #     dict(dtickrange=[1000, 60000], value="%H:%M:%S s"),
    #     dict(dtickrange=[60000, 3600000], value="%H:%M m"),
    #     dict(dtickrange=[3600000, 86400000], value="%H:%M h"),
    #     dict(dtickrange=[86400000, 604800000], value="%e. %b d"),
    #     dict(dtickrange=[604800000, "M1"], value="%e. %b w"),
    #     dict(dtickrange=["M1", "M12"], value="%b '%y M"),
    #     dict(dtickrange=["M12", None], value="%Y Y")
    # ]
)

fig.show()